In [0]:
from pyspark.sql.functions import col, expr, current_timestamp, when, max, date_diff, current_date
from pyspark.sql.window import Window

In [0]:
dept_emp_bronze_df = spark.read.table("employee_catalog.raw.dept_emp")
dept_manager_bronze_df = spark.read.table("employee_catalog.raw.dept_manager")

In [0]:
# Show raw schema 
dept_emp_bronze_df.printSchema()
dept_manager_bronze_df.printSchema()

root
 |-- _airbyte_ab_id: string (nullable = true)
 |-- _airbyte_emitted_at: long (nullable = true)
 |-- _ab_cdc_cursor: string (nullable = true)
 |-- _ab_cdc_deleted_at: string (nullable = true)
 |-- _ab_cdc_log_file: string (nullable = true)
 |-- _ab_cdc_log_pos: integer (nullable = true)
 |-- _ab_cdc_updated_at: timestamp (nullable = true)
 |-- dept_no: string (nullable = true)
 |-- emp_no: integer (nullable = true)
 |-- from_date: date (nullable = true)
 |-- to_date: date (nullable = true)
 |-- _file_name: string (nullable = true)
 |-- load_date: timestamp (nullable = true)

root
 |-- _airbyte_ab_id: string (nullable = true)
 |-- _airbyte_emitted_at: long (nullable = true)
 |-- _ab_cdc_cursor: string (nullable = true)
 |-- _ab_cdc_deleted_at: string (nullable = true)
 |-- _ab_cdc_log_file: string (nullable = true)
 |-- _ab_cdc_log_pos: integer (nullable = true)
 |-- _ab_cdc_updated_at: timestamp (nullable = true)
 |-- dept_no: string (nullable = true)
 |-- emp_no: integer (nullable

In [0]:
employee_dept = dept_emp_bronze_df.union(dept_manager_bronze_df)

In [0]:
display(employee_dept)

_airbyte_ab_id _airbyte_emitted_at _ab_cdc_cursor _ab_cdc_deleted_at _ab_cdc_log_file _ab_cdc_log_pos _ab_cdc_updated_at dept_no emp_no from_date to_date _file_name load_date 81fc151d-65cb-4360-b2ad-f98d4d18458a 1738956715421 null null mysql-bin.000003 66100231 2025-02-07T19:31:55.421Z d005 10001 1986-06-26 9999-01-01 dbfs:/mnt/raw/dept_emp/2025_02_07_1738956719039_0.csv 2025-02-10T20:30:25.745Z a796b60b-af34-40c8-9680-211cedcee5fb 1738956715421 null null mysql-bin.000003 66100231 2025-02-07T19:31:55.421Z d007 10002 1996-08-03 9999-01-01 dbfs:/mnt/raw/dept_emp/2025_02_07_1738956719039_0.csv 2025-02-10T20:30:25.745Z 681911ca-b846-4ff1-816c-4b60ff704c05 1738956715421 null null mysql-bin.000003 66100231 2025-02-07T19:31:55.421Z d004 10003 1995-12-03 9999-01-01 dbfs:/mnt/raw/dept_emp/2025_02_07_1738956719039_0.csv 2025-02-10T20:30:25.745Z daa8f457-3c4b-4a30-9eb6-8b08ccd0b14a 1738956715421 null null mysql-bin.000003 66100231 2025-02-07T19:31:55.421Z d004 10004 1986-12-01 9999-01-01 dbfs:/mnt/raw/dept_emp/2025_02_07_1738956719039_0.csv 2025-02-10T20:30:25.745Z 36fa443d-bdde-4a14-92c5-e128047d1d79 1738956715421 null null mysql-bin.000003 66100231 2025-02-07T19:31:55.421Z d003 10005 1989-09-12 9999-01-01 dbfs:/mnt/raw/dept_emp/2025_02_07_1738956719039_0.csv 2025-02-10T20:30:25.745Z d086875d-043e-4729-a5f6-20929d59cacc 1738956715421 null null mysql-bin.000003 66100231 2025-02-07T19:31:55.421Z d005 10006 1990-08-05 9999-01-01 dbfs:/mnt/raw/dept_emp/2025_02_07_1738956719039_0.csv 2025-02-10T20:30:25.745Z 49ed7e89-c458-4d68-9eca-ad4aee91dd0e 1738956715421 null null mysql-bin.000003 66100231 2025-02-07T19:31:55.421Z d008 10007 1989-02-10 9999-01-01 dbfs:/mnt/raw/dept_emp/2025_02_07_1738956719039_0.csv 2025-02-10T20:30:25.745Z 78f40c44-454c-45e6-b542-aa70f9e49fbb 1738956715421 null null mysql-bin.000003 66100231 2025-02-07T19:31:55.421Z d005 10008 1998-03-11 2000-07-31 dbfs:/mnt/raw/dept_emp/2025_02_07_1738956719039_0.csv 2025-02-10T20:30:25.745Z 2af7d993-818f-49d3-81ef-8972993fd4dc 1738956715421 null null mysql-bin.000003 66100231 2025-02-07T19:31:55.421Z d006 10009 1985-02-18 9999-01-01 dbfs:/mnt/raw/dept_emp/2025_02_07_1738956719039_0.csv 2025-02-10T20:30:25.745Z a3d9215b-ad29-447d-bb8b-5e97e19df832 1738956715421 null null mysql-bin.000003 66100231 2025-02-07T19:31:55.421Z d004 10010 1996-11-24 2000-06-26 dbfs:/mnt/raw/dept_emp/2025_02_07_1738956719039_0.csv 2025-02-10T20:30:25.745Z ec662d4b-4050-4bf3-aa0f-cbb955273627 1738956715421 null null mysql-bin.000003 66100231 2025-02-07T19:31:55.421Z d006 10010 2000-06-26 9999-01-01 dbfs:/mnt/raw/dept_emp/2025_02_07_1738956719039_0.csv 2025-02-10T20:30:25.745Z b857c92e-b4d6-4d5b-8bf6-f8ed59dac0ec 1738956715421 null null mysql-bin.000003 66100231 2025-02-07T19:31:55.421Z d009 10011 1990-01-22 1996-11-09 dbfs:/mnt/raw/dept_emp/2025_02_07_1738956719039_0.csv 2025-02-10T20:30:25.745Z 65df2c20-dc34-44c7-8d3d-ff600d0be9e9 1738956715421 null null mysql-bin.000003 66100231 2025-02-07T19:31:55.421Z d005 10012 1992-12-18 9999-01-01 dbfs:/mnt/raw/dept_emp/2025_02_07_1738956719039_0.csv 2025-02-10T20:30:25.745Z 681eeeb6-539b-43d1-9c5d-524ba1667f12 1738956715421 null null mysql-bin.000003 66100231 2025-02-07T19:31:55.421Z d003 10013 1985-10-20 9999-01-01 dbfs:/mnt/raw/dept_emp/2025_02_07_1738956719039_0.csv 2025-02-10T20:30:25.745Z b72bc8e7-c95d-454d-9913-421315f17c0f 1738956715421 null null mysql-bin.000003 66100231 2025-02-07T19:31:55.421Z d005 10014 1993-12-29 9999-01-01 dbfs:/mnt/raw/dept_emp/2025_02_07_1738956719039_0.csv 2025-02-10T20:30:25.745Z 65b529a0-a7bb-4a69-9998-e1c8de61944d 1738956715421 null null mysql-bin.000003 66100231 2025-02-07T19:31:55.421Z d008 10015 1992-09-19 1993-08-22 dbfs:/mnt/raw/dept_emp/2025_02_07_1738956719039_0.csv 2025-02-10T20:30:25.745Z 3d2a0d7b-ab76-4cf7-a44e-f131ead691e0 1738956715421 null null mysql-bin.000003 66100231 2025-02-07T19:31:55.421Z d007 10016 1998-02-11 9999-01-01 dbfs:/mnt/raw/dept_emp/2025_02_07_1738956719039_0.csv 2025-02-10T20:30:25.745Z 40c1b360-bb80-48a

In [0]:
employee_dept.count()

331627

In [0]:
employee_dept = employee_dept.select(
    expr("TRIM(dept_no)").alias("dept_no"),
    expr("TRIM(emp_no)").alias("emp_no"),
    col("from_date"),
    col("to_date"),
    col("_ab_cdc_updated_at").alias("updated_at")
) \
.withColumn("load_date", current_timestamp()) \
.where(
    col("dept_no").isNotNull() & 
    col("emp_no").isNotNull() & 
    (col("from_date") <= col("to_date"))
    )

In [0]:
window_spec = Window.partitionBy("emp_no")

employee_dept = employee_dept.withColumn(
    "is_current_department", when(col("to_date").isNull() | (col("to_date") == max("to_date").over(window_spec)), "Y")
    .otherwise("N")) \
    .withColumn("department_tenure_days", when(col("to_date") == '9999-01-01', date_diff(current_date(), col("from_date")))
                .otherwise(date_diff(col("to_date"), col("from_date")))) \
    .withColumn("department_tenure_Years", (col("department_tenure_days") / 365).cast("decimal(10,2)"))
    

In [0]:
display(employee_dept.limit(400))

dept_no emp_no from_date to_date updated_at load_date is_current_department department_tenure_days department_tenure_Years d005 100008 1988-03-20 1998-04-13 2025-02-07T19:31:55.421Z 2025-02-11T05:55:23.21Z Y 3676 10.07 d004 100010 1991-10-04 1998-07-06 2025-02-07T19:31:55.421Z 2025-02-11T05:55:23.21Z N 2467 6.76 d009 100010 1998-07-06 9999-01-01 2025-02-07T19:31:55.421Z 2025-02-11T05:55:23.21Z Y 9717 26.62 d004 100014 1990-03-25 2000-01-30 2025-02-07T19:31:55.421Z 2025-02-11T05:55:23.21Z Y 3598 9.86 d005 100021 1991-10-21 9999-01-01 2025-02-07T19:31:55.421Z 2025-02-11T05:55:23.21Z Y 12167 33.33 d002 100022 1985-02-04 9999-01-01 2025-02-07T19:31:55.421Z 2025-02-11T05:55:23.21Z Y 14617 40.05 d005 100025 1995-02-15 9999-01-01 2025-02-07T19:31:55.421Z 2025-02-11T05:55:23.21Z Y 10954 30.01 d005 100029 1991-08-31 1993-11-29 2025-02-07T19:31:55.421Z 2025-02-11T05:55:23.21Z N 821 2.25 d008 100029 1993-11-29 9999-01-01 2025-02-07T19:31:55.421Z 2025-02-11T05:55:23.21Z Y 11397 31.22 d001 100031 1991-04-07 2001-06-24 2025-02-07T19:31:55.421Z 2025-02-11T05:55:23.21Z Y 3731 10.22 d005 100040 1993-05-10 2000-12-09 2025-02-07T19:31:55.421Z 2025-02-11T05:55:23.21Z Y 2770 7.59 d002 100054 1994-10-15 9999-01-01 2025-02-07T19:31:55.421Z 2025-02-11T05:55:23.21Z Y 11077 30.35 d009 100060 1993-12-20 9999-01-01 2025-02-07T19:31:55.421Z 2025-02-11T05:55:23.21Z Y 11376 31.17 d005 100062 1992-05-08 1994-05-05 2025-02-07T19:31:55.421Z 2025-02-11T05:55:23.21Z Y 727 1.99 d007 100068 1991-08-07 1994-09-17 2025-02-07T19:31:55.421Z 2025-02-11T05:55:23.21Z N 1137 3.12 d009 100068 1994-09-17 1996-04-21 2025-02-07T19:31:55.421Z 2025-02-11T05:55:23.21Z Y 582 1.59 d006 100070 1987-09-30 9999-01-01 2025-02-07T19:31:55.421Z 2025-02-11T05:55:23.21Z Y 13649 37.39 d005 100083 1993-02-23 9999-01-01 2025-02-07T19:31:55.421Z 2025-02-11T05:55:23.21Z Y 11676 31.99 d007 100087 1990-03-09 9999-01-01 2025-02-07T19:31:55.421Z 2025-02-11T05:55:23.21Z Y 12758 34.95 d006 10009 1985-02-18 9999-01-01 2025-02-07T19:31:55.421Z 2025-02-11T05:55:23.21Z Y 14603 40.01 d005 100090 1997-04-30 9999-01-01 2025-02-07T19:31:55.421Z 2025-02-11T05:55:23.21Z Y 10149 27.81 d008 100090 1994-11-15 1997-04-30 2025-02-07T19:31:55.421Z 2025-02-11T05:55:23.21Z N 897 2.46 d004 100092 1987-01-28 9999-01-01 2025-02-07T19:31:55.421Z 2025-02-11T05:55:23.21Z Y 13894 38.07 d004 10010 1996-11-24 2000-06-26 2025-02-07T19:31:55.421Z 2025-02-11T05:55:23.21Z N 1310 3.59 d006 10010 2000-06-26 9999-01-01 2025-02-07T19:31:55.421Z 2025-02-11T05:55:23.21Z Y 8996 24.65 d004 100102 1994-08-08 9999-01-01 2025-02-07T19:31:55.421Z 2025-02-11T05:55:23.21Z Y 11145 30.53 d003 100103 1989-09-07 9999-01-01 2025-02-07T19:31:55.421Z 2025-02-11T05:55:23.21Z Y 12941 35.45 d007 100108 1988-09-26 1995-07-30 2025-02-07T19:31:55.421Z 2025-02-11T05:55:23.21Z Y 2498 6.84 d001 100109 1986-09-16 1988-02-10 2025-02-07T19:31:55.421Z 2025-02-11T05:55:23.21Z N 512 1.40 d007 100109 1988-02-10 9999-01-01 2025-02-07T19:31:55.421Z 2025-02-11T05:55:23.21Z Y 13516 37.03 d009 10011 1990-01-22 1996-11-09 2025-02-07T19:31:55.421Z 2025-02-11T05:55:23.21Z Y 2483 6.80 d007 100111 1986-07-31 9999-01-01 2025-02-07T19:31:55.421Z 2025-02-11T05:55:23.21Z Y 14075 38.56 d007 100116 1992-03-28 9999-01-01 2025-02-07T19:31:55.421Z 2025-02-11T05:55:23.21Z Y 12008 32.90 d005 10012 1992-12-18 9999-01-01 2025-02-07T19:31:55.421Z 2025-02-11T05:55:23.21Z Y 11743 32.17 d009 100120 1993-03-06 9999-01-01 2025-02-07T19:31:55.421Z 2025-02-11T05:55:23.21Z Y 11665 31.96 d005 100124 1987-08-16 9999-01-01 2025-02-07T19:31:55.421Z 2025-02-11T05:55:23.21Z Y 13694 37.52 d001 100125 1988-02-13 9999-01-01 2025-02-07T19:31:55.421Z 2025-02-11T05:55:23.21Z Y 13513 37.02 d005 100128 1999-05-31 2000-09-25 2025-02-07T19:31:55.421Z 2025-02-11T05:55:23.21Z N 483 1.32 d008 100128 2000-09-25 2000-10-06 2025-02-07T19:31:55.421Z 2025-02-11T05:55:23.21Z Y 11 0.03 d009 100129 1997-05-25 9999-01-01 2025-02-07T19:31:55.421Z 2025-02-11T05:55:23.21Z Y 10124 27.74 d005 100130 1987-11-10 9999-01-01 2025-02-

In [0]:
spark.sql(f"CREATE SCHEMA IF NOT EXISTS employee_catalog.silver")

DataFrame[]

In [0]:
employee_dept.write \
    .option("mergeSchema", True) \
    .mode("overwrite") \
    .saveAsTable("employee_catalog.silver.employee_departmemnt")